# SAR-LRA Tool for Google Colaboratory

This notebook facilitates the acquisition of Sentinel-1 SAR composite imagery for the VV_VH combination, encompassing both ascending and descending orbits, which can then be utilized to deploy the models.

Without modifications the notebook will predict in Taiwan.

### IMPORTANT:
Select a runtime with large RAM (such as TPU), otherwise the processing will brake.

It'll ask you to restart. You do not need to.

In [ ]:
# # install some libraries

# !pip install geedim
# !pip install leafmap==0.22.0
# !pip install geemap==0.24.1
# !pip install -U geemap
# !pip install earthengine-api
# !pip install rasterio
# !pip install opencv-python-headless
# !pip install requests
# !pip install tensorflow==2.12

In [ ]:
import leafmap          
import geemap           
import ee               
import numpy as np      
import pandas as pd     
import rasterio
import tensorflow as tf
import numpy as np
import cv2
from utils import build_s1_rel_composites, run_lra_inference_per_rel

# Print versions
print("leafmap:", leafmap.__version__)           # Version 0.22.0
print("geemap:", geemap.__version__)             # Version 0.35.1
print("Earth Engine API:", ee.__version__)       # Version 1.5.3
print("numpy:", np.__version__)                  # Version 1.26.4
print("pandas:", pd.__version__)                 # Version 2.2.2
print("Rasterio version:", rasterio.__version__) # Version 1.4.3
print("TensorFlow version:", tf.__version__)     # Version 2.12.0
print("NumPy version:", np.__version__)          # Version 1.26.4
print("OpenCV version:", cv2.__version__)        # Version 4.11.0

## 2. Autenticate and initialize the Google Earth Engine

In [ ]:
ee.Authenticate()
ee.Initialize(project='ee-lorenava-learning-sar') # replace with the name of your GEE project

## 3. Initialize and Define Area of Interest (AoI)

This section initializes a `Map` instance using the `geemap` library and centers it on a global view with a satellite basemap. The map will help define the Area of Interest (AOI).

### Instructions:
1. Use the map tools on the left to draw a single rectangular box defining your AOI.
2. Use the globe icon on the top left to search for specific locations if needed.



In [ ]:
# Create a Map instance
Map = geemap.Map()

# Add a satellite basemap for visualization (similar to Google Earth)
Map.add_basemap('HYBRID')

# Center the map globally
Map.setCenter(0, 0, 2)  # Center on the world with zoom level 2

# Display the map for user interaction
Map

## 4. Define temporal buffers and temporal stacks
Change the dates according to your event.

IMPORTANT: The landslides MUST be occurred in between the pre_end and post_start dates.

In [ ]:
pre_stack_end = '2021-08-13'
post_stack_start = '2021-08-17'

build_s1_rel_composites(
    geometry=ee.FeatureCollection(Map.draw_features),     # your ee.Geometry / Feature / FeatureCollection
    pre_stack_end=pre_stack_end,       # "YYYY-MM-DD"
    post_stack_start=post_stack_start, # "YYYY-MM-DD"
    pre_days=60,
    post_days=12,
    orbits=("DESCENDING","ASCENDING"),
    project_path="",
    list_images=True,                  # set False to silence per-image prints
    fishnet_h=0.5, fishnet_v=0.5, fishnet_delta=1,
    scale=10, crs_epsg="EPSG:4326", error_margin_m=1,
    initialize_ee=False
)

### Descending orbit

In [ ]:
run_lra_inference_per_rel(
    place="Haiti",
    orbit="DESCENDING",
    base_dir="deploy/VV_VH/60_12",
    weights_url="https://github.com/lorenzonava96/SAR-and-DL-for-Landslide-Rapid-Assessment/raw/main/SAR-LRA%20Tool%20V1/model_weights/VV_VH_60_nn_noSlope_DESCENDING_60_12_5_size_64_filters_64_batch_size_512_lr_0.001_dropout_0.7_fil1_3_fil2_3_fil3_3.hdf5",
    # or weights_local_path="path/to/local_descending_weights.hdf5",
    size=64,
    channels=4,
    prob_thresh=0.6,
    nms_overlap=0.1,
    batch_size=512,
    filtersFirstLayer=64
)

### Ascending orbit

In [ ]:
run_lra_inference_per_rel(
    place="Haiti",
    orbit="ASCENDING",
    base_dir="deploy/VV_VH/60_12",
    weights_url="https://github.com/lorenzonava96/SAR-and-DL-for-Landslide-Rapid-Assessment/raw/main/SAR-LRA%20Tool%20V1/model_weights/VV_VH_60_nn_noSlope_ASCENDING_60_12_6_size_64_filters_32_batch_size_512_lr_0.001_dropout_0.7_fil1_3_fil2_3_fil3_3.hdf5",
    # or weights_local_path="path/to/local_descending_weights.hdf5",
    size=64,
    channels=4,
    prob_thresh=0.6,
    nms_overlap=0.1,
    batch_size=512,
    filtersFirstLayer=32
)